In [1]:
import yfinance as yf
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.graph_objects as go

In [2]:
pd.options.mode.chained_assignment = None

In [3]:
symbol = "IWQU"
exchange = "MI"
ticker_str = symbol + "." + exchange

In [4]:
ticker_str = "^GSPC"

In [5]:
ticker = yf.Ticker(ticker_str)

In [6]:
history = ticker.history("max")

In [7]:
history["Month"] = history.index.to_period("M")

In [8]:
history

Open         High          Low        Close      Volume  \
Date                                                                         
1950-01-03    16.660000    16.660000    16.660000    16.660000     1260000   
1950-01-04    16.850000    16.850000    16.850000    16.850000     1890000   
1950-01-05    16.930000    16.930000    16.930000    16.930000     2550000   
1950-01-06    16.980000    16.980000    16.980000    16.980000     2010000   
1950-01-09    17.080000    17.080000    17.080000    17.080000     2520000   
...                 ...          ...          ...          ...         ...   
2022-01-26  4408.430176  4453.229980  4304.799805  4349.930176  4046270000   
2022-01-27  4380.580078  4428.740234  4309.500000  4326.509766  4074330000   
2022-01-28  4336.189941  4432.720215  4292.459961  4431.850098  3936030000   
2022-01-31  4431.790039  4516.890137  4414.020020  4515.549805  4001950000   
2022-02-01  4519.569824  4549.180176  4483.529785  4546.959961  2164038000   

            Dividends  Stock Splits    Month  
Date                                          
1950-01-03          0             0  1950-01  
1950-01-04          0             0  1950-01  
1950-01-05          0             0  1950-01  
1950-01-06          0             0  1950-01  
1950-01-09          0             0  1950-01  
...               ...           ...      ...  
2022-01-26          0             0  2022-01  
2022-01-27          0             0  2022-01  
2022-01-28          0             0  2022-01  
2022-01-31          0             0  2022-01  
2022-02-01          0             0  2022-02  

[18139 rows x 8 columns]

In [9]:
history = history.loc[:, ["Close", "Month"]]

Remove first uncomplete month

In [10]:
last_dom = history.index[0] + pd.tseries.offsets.BMonthEnd()

In [11]:
history = history[history.index > last_dom]

Remove last uncomplete month

In [12]:
first_dom = history.index[-1].to_period("M").to_timestamp()

In [13]:
history = history[history.index < first_dom]

In [14]:
history

Close    Month
Date                            
1950-02-01    17.049999  1950-02
1950-02-02    17.230000  1950-02
1950-02-03    17.290001  1950-02
1950-02-06    17.320000  1950-02
1950-02-07    17.230000  1950-02
...                 ...      ...
2022-01-25  4356.450195  2022-01
2022-01-26  4349.930176  2022-01
2022-01-27  4326.509766  2022-01
2022-01-28  4431.850098  2022-01
2022-01-31  4515.549805  2022-01

[18117 rows x 2 columns]

In [15]:
month_groups = pd.DataFrame(index=history["Month"].unique(), columns=["MonthSum", "MonthCount"])

In [16]:
month_groups["MonthSum"] = history.groupby("Month")["Close"].sum()
month_groups["MonthCount"] = history.groupby("Month")["Close"].count()

In [17]:
sma = month_groups.rolling(10).sum().dropna()

In [18]:
sma["SMA"] = sma["MonthSum"] / sma["MonthCount"]

In [19]:
sma.drop(["MonthSum", "MonthCount"], axis=1, inplace=True)

In [20]:
history = history[history.index >= sma.index[0].to_timestamp()]

In [21]:
sma.set_index(history.reset_index().groupby("Month").last()["Date"], inplace=True)

In [22]:
sma["Close"] = history["Close"]

In [23]:
sma["In"] = (sma["Close"] > sma["SMA"]).astype(int)

In [24]:
sma["Buy"] = sma["In"].diff() == 1
sma["Sell"] = sma["In"].diff() == -1

TODO: Introdurre 1-week delay

In [25]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=history.index, y=history["Close"],
                    mode="lines",
                    name="Close price"))
fig.add_trace(go.Scatter(x=sma.index, y=sma["SMA"],
                    mode="lines",
                    name="10 Months SMA"))
fig.add_trace(go.Scatter(x=sma[sma["Buy"]].index, y=sma[sma["Buy"]]["SMA"] * 1.2,
                    mode="markers",
                    marker_color="green",
                    marker_symbol="triangle-down",
                    name="Buy signals"))
fig.add_trace(go.Scatter(x=sma[sma["Sell"]].index, y=sma[sma["Sell"]]["SMA"] * 1.2,
                    mode="markers",
                    marker_color="red",
                    marker_symbol="triangle-down",
                    name="Sell signals"))
fig.update_layout(title=ticker_str, xaxis_title="Year", yaxis_title="Log Close Price")
fig.update_yaxes(type="log")
fig.show()

In [26]:
history["In"] = sma["In"].diff()

In [27]:
history["In"] = history["In"].fillna(0)

In [28]:
first_sell = history[history["In"] == -1].index[0]
first_buy = history[history["In"] == 1].index[0]

In [29]:
if first_sell < first_buy:
    history.loc[history.index[0], "In"] = 1

In [30]:
history["In"] = history["In"].cumsum()

In [31]:
history["ChangePct"] = history["Close"].pct_change() + 1
history.loc[history.index[0], "ChangePct"] = 1

In [32]:
history["ChangePctStrategy"] = history["ChangePct"]
history.loc[history["In"] != 1, "ChangePctStrategy"] = 1

In [33]:
bh_evolution = history["ChangePct"].cumprod() * history.iloc[0,:]["Close"]
strategy_evolution = history["ChangePctStrategy"].cumprod() * history.iloc[0,:]["Close"]
flat_zones = pd.Series(index=history.index, data=np.nan)
flat_zones[history["In"] != 1] = strategy_evolution[history["In"] != 1]

In [34]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=history.index, y=bh_evolution,
                    mode="lines",
                    name="Original"))
fig.add_trace(go.Scatter(x=history.index, y=strategy_evolution,
                    mode="lines",
                    name="Strategy"))
fig.add_trace(go.Scatter(x=flat_zones.index, y=flat_zones,
                    mode="lines",
                    name="Flat zones"))
fig.update_layout(title=ticker_str, xaxis_title="Year", yaxis_title="Log Close Price")
fig.update_yaxes(type="log")
fig.show()